In [1]:
import os
import numpy as np
import pandas as pd
import torch
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler
import os

# Importing the T5 modules from huggingface/transformers
from transformers import MT5Tokenizer, MT5ForConditionalGeneration, T5Model
from rich.table import Column, Table
from rich import box
from rich.console import Console

# define a rich console logger
console=Console(record=True)

def display_df(df):
    """display dataframe in ASCII format"""

    console=Console()
    table = Table(Column("source_text", justify="center" ), Column("target_text", justify="center"), title="Sample Data",pad_edge=False, box=box.ASCII)

    for i, row in enumerate(df.values.tolist()):
        table.add_row(row[0], row[1])

    console.print(table)

training_logger = Table(Column("Epoch", justify="center" ), 
                        Column("Steps", justify="center"),
                        Column("Loss", justify="center"), 
                        title="Training Status",pad_edge=False, box=box.ASCII)


In [2]:
from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'

In [3]:
class YourDataSetClass(Dataset):
    def __init__(self, dataframe, tokenizer, source_len, target_len, source_text, target_text):
        self.tokenizer = tokenizer
        self.data = dataframe
        self.source_len = source_len
        self.summ_len = target_len
        self.target_text = self.data[target_text]
        self.source_text = self.data[source_text]

    def __len__(self):
        return len(self.target_text)

    def __getitem__(self, index):
        source_text = str(self.source_text[index])
        target_text = str(self.target_text[index])

        #cleaning data so as to ensure data is in string type
        source_text = ' '.join(source_text.split())
        target_text = ' '.join(target_text.split())

        source = self.tokenizer.batch_encode_plus([source_text], max_length= self.source_len, pad_to_max_length=True, truncation=True, padding="max_length", return_tensors='pt')
        target = self.tokenizer.batch_encode_plus([target_text], max_length= self.summ_len, pad_to_max_length=True, truncation=True, padding="max_length", return_tensors='pt')

        source_ids = source['input_ids'].squeeze()
        source_mask = source['attention_mask'].squeeze()
        target_ids = target['input_ids'].squeeze()
        target_mask = target['attention_mask'].squeeze()

        return {
            'source_ids': source_ids.to(dtype=torch.long), 
            'source_mask': source_mask.to(dtype=torch.long), 
            'label_ids': target_ids.to(dtype=torch.long),
            'decoder_attention_mask': target_mask.to(dtype=torch.long)
        }

In [4]:
def train(epoch, tokenizer, model, device, loader, optimizer):
    for _, data in enumerate(loader, 0):
        labels = data["label_ids"].to(device, dtype=torch.long)
        ids = data["source_ids"].to(device, dtype=torch.long)
        mask = data["source_mask"].to(device, dtype=torch.long)
        decoder_attention_mask= data["decoder_attention_mask"].to(device, dtype=torch.long)

        outputs = model(
            input_ids=ids,
            attention_mask=mask,
            labels=labels,
            decoder_attention_mask=decoder_attention_mask
        )
        loss = outputs[0]

        if _ % 100 == 0:
            training_logger.add_row(str(epoch), str(_), str(loss))
            console.print(training_logger)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

In [5]:
def validate(epoch, tokenizer, model, device, loader):
    model.eval()
    predictions = []
    actuals = []
    with torch.no_grad():
          for _, data in enumerate(loader, 0):
                y = data['label_ids'].to(device, dtype = torch.long)
                ids = data['source_ids'].to(device, dtype = torch.long)
                mask = data['source_mask'].to(device, dtype = torch.long)

                generated_ids = model.generate(
                    input_ids = ids,
                    attention_mask = mask, 
                    max_length=250, 
                    num_beams=2,
                    repetition_penalty=2.5, 
                    length_penalty=1.0, 
                    early_stopping=True
                    )
                preds = [tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in generated_ids]
                target = [tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True)for t in y]
                if _%512==0:
                    console.print(f'Completed {_}')

                predictions.extend(preds)
                actuals.extend(target)
    return predictions, actuals


In [13]:
def T5Trainer(
    dataframe, source_text, target_text, model_params, output_dir="./outputs/"
):

    """
    T5 trainer

    """

    # Set random seeds and deterministic pytorch for reproducibility
    torch.manual_seed(model_params["SEED"])  # pytorch random seed
    np.random.seed(model_params["SEED"])  # numpy random seed
    torch.backends.cudnn.deterministic = True

    # logging
    console.log(f"""[Model]: Loading {model_params["MODEL"]}...\n""")

    # tokenzier for encoding the text
    tokenizer = MT5Tokenizer.from_pretrained(model_params["MODEL"])

    # Defining the model. We are using t5-base model and added a Language model layer on top for generation of Summary.
    # Further this model is sent to device (GPU/TPU) for using the hardware.
    model = MT5ForConditionalGeneration.from_pretrained(model_params["MODEL"])
    #model = T5Model.from_pretrained(model_params["MODEL"])
    model = model.to(device)

    # logging
    console.log(f"[Data]: Reading data...\n")

    # Importing the raw dataset
    dataframe = dataframe[[source_text, target_text]]
    display_df(dataframe.head(2))

    # Creation of Dataset and Dataloader
    # Defining the train size. So 80% of the data will be used for training and the rest for validation.
    train_size = 0.8
    train_dataset = dataframe.sample(frac=train_size, random_state=model_params["SEED"])
    val_dataset = dataframe.drop(train_dataset.index).reset_index(drop=True)
    train_dataset = train_dataset.reset_index(drop=True)

    console.print(f"FULL Dataset: {dataframe.shape}")
    console.print(f"TRAIN Dataset: {train_dataset.shape}")
    console.print(f"TEST Dataset: {val_dataset.shape}\n")

    # Creating the Training and Validation dataset for further creation of Dataloader
    training_set = YourDataSetClass(
        train_dataset,
        tokenizer,
        model_params["MAX_SOURCE_TEXT_LENGTH"],
        model_params["MAX_TARGET_TEXT_LENGTH"],
        source_text,
        target_text
    )
    val_set = YourDataSetClass(
        val_dataset,
        tokenizer,
        model_params["MAX_SOURCE_TEXT_LENGTH"],
        model_params["MAX_TARGET_TEXT_LENGTH"],
        source_text,
        target_text
    )

    # Defining the parameters for creation of dataloaders
    train_params = {
        "batch_size": model_params["TRAIN_BATCH_SIZE"],
        "shuffle": True,
        "num_workers": 0,
    }

    val_params = {
        "batch_size": model_params["VALID_BATCH_SIZE"],
        "shuffle": False,
        "num_workers": 0,
    }

    # Creation of Dataloaders for testing and validation. This will be used down for training and validation stage for the model.
    training_loader = DataLoader(training_set, **train_params)
    val_loader = DataLoader(val_set, **val_params)

    # Defining the optimizer that will be used to tune the weights of the network in the training session.
    optimizer = torch.optim.Adam(
        params=model.parameters(), lr=model_params["LEARNING_RATE"]
    )

    # Training loop
    console.log(f"[Initiating Fine Tuning]...\n")

    for epoch in range(model_params["TRAIN_EPOCHS"]):
        train(epoch, tokenizer, model, device, training_loader, optimizer)

    console.log(f"[Saving Model]...\n")
    # Saving the model after training
    path = os.path.join(output_dir, "model_files")
    model.save_pretrained(path)
    tokenizer.save_pretrained(path)

    # evaluating test dataset
    console.log(f"[Initiating Validation]...\n")
    for epoch in range(model_params["VAL_EPOCHS"]):
        predictions, actuals = validate(epoch, tokenizer, model, device, val_loader)
        final_df = pd.DataFrame({"Generated Text": predictions, "Actual Text": actuals})
        final_df.to_csv(os.path.join(output_dir, "predictions.csv"))

    console.save_text(os.path.join(output_dir, "logs.txt"))

    console.log(f"[Validation Completed.]\n")
    console.print(
        f"""[Model] Model saved @ {os.path.join(output_dir, "model_files")}\n"""
    )
    console.print(
        f"""[Validation] Generation on Validation data saved @ {os.path.join(output_dir,'predictions.csv')}\n"""
    )
    console.print(f"""[Logs] Logs saved @ {os.path.join(output_dir,'logs.txt')}\n""")

In [19]:
model_params = {
    "MODEL": "josmunpen/mt5-small-spanish-summarization",  # model_type: t5-base/t5-large
    "TRAIN_BATCH_SIZE": 8,  # training batch size
    "VALID_BATCH_SIZE": 16,  # validation batch size
    "TRAIN_EPOCHS": 3,  # number of training epochs
    "VAL_EPOCHS": 1,  # number of validation epochs
    "LEARNING_RATE": 1e-4,  # learning rate
    "MAX_SOURCE_TEXT_LENGTH": 177,  # max length of source text
    "MAX_TARGET_TEXT_LENGTH": 47,  # max length of target text
    "SEED": 47,  # set seed for reproducibility
}

In [20]:
train_df = pd.read_csv('train_es_df.csv')
train_df["input_text"] = train_df['prefix']+": "+ train_df["input_text"]
train_df = train_df[train_df["target"]!="class: -1"]
train_df = train_df[train_df["prefix"]!="authorship identification"]
train_df = train_df.drop(columns=['Unnamed: 0','index'])
train_df = train_df.sample(frac=1, random_state=4).reset_index(drop=True)

In [21]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 67975 entries, 0 to 67974
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   input_text  67975 non-null  object
 1   prefix      67975 non-null  object
 2   target      67975 non-null  object
dtypes: object(3)
memory usage: 1.6+ MB


In [22]:
train_df.head()

input_text                prefix  \
0  hater classification: rt user con cariño a las...  hater classification   
1  hater classification: hashtag los giliprogres ...  hater classification   
2  hater classification: user no pierdo el tiempo...  hater classification   
3  hater classification: cada vez q escribo un tw...  hater classification   
4  topic classification: user y ricos comprando a...  topic classification   

       target  
0  hatespeach  
1  hatespeach  
2  hatespeach  
3     neutral  
4   class: 51

In [ ]:

T5Trainer(
    dataframe=train_df,
    source_text="input_text",
    target_text="target",
    model_params=model_params,
    output_dir="outputs",
)


[16:45:31] [Model]: Loading                                <ipython-input-13-c6e257bed25e>:16
           josmunpen/mt5-small-spanish-summarization...

[16:47:20] [Data]: Reading data...                         <ipython-input-13-c6e257bed25e>:28

                                         Sample Data                                         
+-------------------------------------------------------------------------------------------+
|                                 source_text                                  | target_text|
|------------------------------------------------------------------------------+------------|
|   hater classification: rt user con cariño a las organizaciones del 8m en    | hatespeach |
|                                 madrid url                                   |            |
|hater classification: hashtag los giliprogres de turno os follaron muy mal de | hatespeach |
|  ahí viene ese odio al hombre la mayoría no os toca ni con un palo cerdas    |            |
+-------------------------------------------------------------------------------------------+

FULL Dataset: (67975, 2)

TRAIN Dataset: (54380, 2)

...

                               Training Status                               
+---------------------------------------------------------------------------+
|Epoch | Steps |                            Loss                            |
|------+-------+------------------------------------------------------------|
|  0   |   0   | tensor(25.1517, device='cuda:0', grad_fn=<NllLossBackward>)|
|  0   |  100  | tensor(0.1794, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  200  | tensor(0.0282, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  300  | tensor(0.0725, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  400  | tensor(0.0365, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  500  | tensor(0.0310, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  600  | tensor(0.0433, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  700  | tensor(0.0484, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  800  | tensor(0.0459, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  900  | tensor(0.0435, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1000  | tensor(0.0204, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1100  | tensor(0.0598, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1200  | tensor(0.0682, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1300  | tensor(0.0555, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1400  | tensor(0.0356, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1500  | tensor(0.0505, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1600  | tensor(0.0346, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1700  | tensor(0.0474, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1800  | tensor(0.0561, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1900  | tensor(0.0613, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2000  | tensor(0.0419, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2100  | tensor(0.0602, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2200  | tensor(0.0209, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2300  | tensor(0.0518, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2400  | tensor(0.0489, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2500  | tensor(0.0513, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2600  | tensor(0.0282, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2700  | tensor(0.0243, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2800  | tensor(0.0264, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2900  | tensor(0.0483, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3000  | tensor(0.0291, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3100  | tensor(0.0481, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3200  | tensor(0.0166, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3300  | tensor(0.0292, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3400  | tensor(0.0460, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3500  | tensor(0.0161, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3600  | tensor(0.0425, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3700  | tensor(0.0690, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3800  | tensor(0.0301, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3900  | tensor(0.0373, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4000  | tensor(0.0271, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4100  | tensor(0.0659, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4200  | tensor(0.0223, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4300  | tensor(0.0250, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4400  | tensor(0.0291, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4500  | tensor(0.0400, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4600  | tensor(0.0588, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4700  | tenso

                               Training Status                               
+---------------------------------------------------------------------------+
|Epoch | Steps |                            Loss                            |
|------+-------+------------------------------------------------------------|
|  0   |   0   | tensor(25.1517, device='cuda:0', grad_fn=<NllLossBackward>)|
|  0   |  100  | tensor(0.1794, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  200  | tensor(0.0282, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  300  | tensor(0.0725, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  400  | tensor(0.0365, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  500  | tensor(0.0310, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  600  | tensor(0.0433, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  700  | tensor(0.0484, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  800  | tensor(0.0459, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   |  900  | tensor(0.0435, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1000  | tensor(0.0204, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1100  | tensor(0.0598, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1200  | tensor(0.0682, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1300  | tensor(0.0555, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1400  | tensor(0.0356, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1500  | tensor(0.0505, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1600  | tensor(0.0346, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1700  | tensor(0.0474, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1800  | tensor(0.0561, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 1900  | tensor(0.0613, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2000  | tensor(0.0419, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2100  | tensor(0.0602, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2200  | tensor(0.0209, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2300  | tensor(0.0518, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2400  | tensor(0.0489, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2500  | tensor(0.0513, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2600  | tensor(0.0282, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2700  | tensor(0.0243, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2800  | tensor(0.0264, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 2900  | tensor(0.0483, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3000  | tensor(0.0291, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3100  | tensor(0.0481, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3200  | tensor(0.0166, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3300  | tensor(0.0292, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3400  | tensor(0.0460, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3500  | tensor(0.0161, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3600  | tensor(0.0425, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3700  | tensor(0.0690, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3800  | tensor(0.0301, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 3900  | tensor(0.0373, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4000  | tensor(0.0271, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4100  | tensor(0.0659, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4200  | tensor(0.0223, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4300  | tensor(0.0250, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4400  | tensor(0.0291, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4500  | tensor(0.0400, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4600  | tensor(0.0588, device='cuda:0', grad_fn=<NllLossBackward>) |
|  0   | 4700  | tenso

[18:37:15] [Saving Model]...                               <ipython-input-13-c6e257bed25e>:91

[18:37:18] [Initiating Validation]...                      <ipython-input-13-c6e257bed25e>:98

Completed 0

In [ ]:



+

